In [1]:
import pandas as pd
import os
from tqdm.notebook import tqdm
from scipy.stats import combine_pvalues
from statsmodels.stats.multitest import multipletests
import numpy as np

tqdm.pandas()

# ENCODE DNase I allelic imbalance data

### If you have any questions, please reach us at:
+ <b> sabramov@altius.org </b> Sergey Abramov 
+ <b> sboytsov@altius.org </b> Alexandr Boytsov


# Accessing the data

The data is stored at https://resources.altius.org/~jvierstra/projects/encode4-allelic-imbalance-v1<br>
The directory contains:
+ Metadata file: `metadata.tsv`
+ All tested variants: `cav_pvalues.1010.melt.sorted.bed.gz`
+ Readme file: `README.tsv`
+ This notebook

## Metadata file
+ `ag_id` - a unique identifier of a sample
+ `idniv_id` - individual genotype id. Samples with the same indiv_id have very similar genotype (not necessarily the same cell type)

In [2]:
!wget https://resources.altius.org/~jvierstra/projects/encode4-allelic-imbalance-v1/metadata.tsv
meta = pd.read_table('metadata.tsv')
meta

--2022-10-10 22:52:28--  https://resources.altius.org/~jvierstra/projects/encode4-allelic-imbalance-v1/metadata.tsv
Resolving resources.altius.org (resources.altius.org)... 10.174.2.79
Connecting to resources.altius.org (resources.altius.org)|10.174.2.79|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 227346 (222K) [text/tab-separated-values]
Saving to: ‘metadata.tsv.1’

100%[======================================>] 227,346     --.-K/s   in 0.005s  

2022-10-10 22:52:28 (43.0 MB/s) - ‘metadata.tsv.1’ saved [227346/227346]



ag_id    indiv_id    taxonomy_name ontology_id            ontology_term  \
0    70947  INDIV_0007  h.Macrophage.M2  CL:0000862    suppressor macrophage   
1    70948  INDIV_0010  h.Macrophage.M2  CL:0000862    suppressor macrophage   
2    70891  INDIV_0029  h.Macrophage.M1  CL:0000863  inflammatory macrophage   
3    70883  INDIV_0029          h.CD14+  CL:0001054   CD14-positive monocyte   
4    70847  INDIV_0029  h.Macrophage.M2  CL:0000862    suppressor macrophage   
..     ...         ...              ...         ...                      ...   
843  70842  INDIV_1830  h.Macrophage.M2  CL:0000862    suppressor macrophage   
844  70832  INDIV_1830  h.Macrophage.M1  CL:0000863  inflammatory macrophage   
845  70806  INDIV_1830  h.Macrophage.M2  CL:0000862    suppressor macrophage   
846  70833  INDIV_1830  h.Macrophage.M1  CL:0000863  inflammatory macrophage   
847  70878  INDIV_1830          h.CD14+  CL:0001054   CD14-positive monocyte   

            system subsystem  organ organ_region  side_position  ...  \
0    Hematopoietic   Myeloid  Blood          NaN            NaN  ...   
1    Hematopoietic   Myeloid  Blood          NaN            NaN  ...   
2    Hematopoietic   Myeloid  Blood          NaN            NaN  ...   
3    Hematopoietic   Myeloid  Blood          NaN            NaN  ...   
4    Hematopoietic   Myeloid  Blood          NaN            NaN  ...   
..             ...       ...    ...          ...            ...  ...   
843  Hematopoietic   Myeloid  Blood          NaN            NaN  ...   
844  Hematopoietic   Myeloid  Blood          NaN            NaN  ...   
845  Hematopoietic   Myeloid  Blood          NaN            NaN  ...   
846  Hematopoietic   Myeloid  Blood          NaN            NaN  ...   
847  Hematopoietic   Myeloid  Blood          NaN            NaN  ...   

    donor_health_condition                        vendor_name perturbation  \
0                      NaN  Fred Hutch Cancer Research Center      control   
1                      NaN  Fred Hutch Cancer Research Center     biologic   
2                      NaN  Fred Hutch Cancer Research Center      control   
3                      NaN  Fred Hutch Cancer Research Center      control   
4                      NaN  Fred Hutch Cancer Research Center     biologic   
..                     ...                                ...          ...   
843                    NaN  Fred Hutch Cancer Research Center      control   
844                    NaN  Fred Hutch Cancer Research Center      control   
845                    NaN  Fred Hutch Cancer Research Center     biologic   
846                    NaN  Fred Hutch Cancer Research Center     biologic   
847                    NaN  Fred Hutch Cancer Research Center      control   

    treatment_name         treatment_details dose dose_units hotspot2_spot  \
0            Media           RPMI-1640 Media  NaN        NaN        0.7127   
1              LPS  Lipopolysaccharide (LPS)  NaN        NaN        0.6586   
2             DMSO                      DMSO  NaN        NaN        0.6179   
3             DMSO                      DMSO  NaN        NaN        0.2774   
4              LPS  Lipopolysaccharide (LPS)  NaN        NaN        0.6872   
..             ...                       ...  ...        ...           ...   
843           DMSO                      DMSO  NaN        NaN        0.4783   
844           DMSO                      DMSO  NaN        NaN        0.5235   
845            LPS  Lipopolysaccharide (LPS)  NaN        NaN        0.4926   
846            LPS  Lipopolysaccharide (LPS)  NaN        NaN        0.3793   
847      untreated                 untreated  NaN        NaN        0.4295   

    nuclear_percent_duplication  paired_nuclear_align  
0                       19.5437           242891954.0  
1                       14.7689           187143892.0  
2                       50.9084           250837530.0  
3                       26.0185           363144194.0  
4                       4

## Variants format
### Variants are stored in the bed-like format:
+ `#chr, start, end`: genomic position of the SNV, hg38 genome assembly;
+ `ID`: rsSNP ID of the SNV according to the dbSNP build 151;
+ `ref`: reference allele (A,C,G, or T, according to hg38);
+ `alt`: alternative allele;
+ `ref_counts, alt_counts`: number of reads mapped to the alleles;
+ `sample_id`: unique identifier of the sample, corresponds to `ag_id` in metadata file
+ `BAD`: <b>b</b>ackground <b>a</b>llelic <b>d</b>osage estimation at the variant. Higher BAD values correspond to the higher contribution of aneuploidy and local copy-number variants. BAD scores serve as a baseline when estimating the statistical significance and the effect size of each tested variant. BAD=1 in case of diploid and BAD=2 in case of triploid.

+ `es`: Effect size of allelic imbalance at the variant, log2. Positive values indicate imbalance favouring the reference allele. Corrected for BAD.
+ `pval_ref, pval_alt`: allele-wise P-value estimations of one-sided tests. Lower P-values indicate the preference of the corresponding allele, e.g. low `pval_ref` means the variant is <b>reference</b> imbalanced


### You can download the variants in a specific region using tabix
`tabix https://resources.altius.org/~jvierstra/projects/encode4-allelic-imbalance-v1/cav_pvalues.1010.melt.sorted.bed.gz ${region} > cav_pvalues_${region}.bed`


In [3]:
columns = ['#chr', 'start', 'end', 'ID', 'ref', 'alt', 'ref_counts', 'alt_counts',
       'sample_id', 'BAD', 'es', 'pval_ref', 'pval_alt']

!tabix https://resources.altius.org/~jvierstra/projects/encode4-allelic-imbalance-v1/cav_pvalues.1010.melt.sorted.bed.gz chr1:1-5000000 > cav_pvalues.chr1_1-5000000.bed

    
tested_variants = pd.read_table('cav_pvalues.chr1_1-5000000.bed', header=None, names=columns)
tested_variants

#chr    start      end           ID ref alt  ref_counts  alt_counts  \
0      chr1    10108    10109  rs376007522   A   T          14          39   
1      chr1    10108    10109  rs376007522   A   T           6          21   
2      chr1    10468    10469  rs370233998   C   G          10           6   
3      chr1    10588    10589            .   C   T          10           6   
4      chr1    10588    10589            .   C   T           5           5   
...     ...      ...      ...          ...  ..  ..         ...         ...   
39253  chr1  4978032  4978033    rs6666618   A   C           8          10   
39254  chr1  4978563  4978564   rs12564764   G   A           5           6   
39255  chr1  4984909  4984910    rs1106585   G   A          13          11   
39256  chr1  4984969  4984970    rs1106586   G   A          12          11   
39257  chr1  4984969  4984970    rs1106586   G   A           7           5   

       sample_id  BAD        es  pval_ref  pval_alt  
0          72389  1.0 -1.478047  0.999866  0.000401  
1          72386  1.0 -1.807355  0.999398  0.002938  
2          72737  1.5  0.344980  0.432531  0.837543  
3          72755  2.5 -0.518969  0.785226  0.603204  
4          72756  2.5  0.000000  1.000000  1.000000  
...          ...  ...       ...       ...       ...  
39253      79966  1.5 -0.096943  0.629698  0.558183  
39254      79994  1.5 -0.146042  1.000000  0.671661  
39255      80031  1.0  0.241008  0.419653  0.729898  
39256      80030  1.5  0.008538  0.570281  0.544987  
39257      80031  1.0  0.485427  0.428571  1.000000  

[39258 rows x 13 columns]

### `sample_id` is a unique identifier of the dataset; it corresponds to `ag_id` in metadata file

In [4]:
tested_variants.merge(meta, left_on='sample_id', right_on='ag_id')

#chr    start      end           ID ref alt  ref_counts  alt_counts  \
0      chr1    10108    10109  rs376007522   A   T          14          39   
1      chr1   183628   183629   rs71267774   G   A          17           9   
2      chr1   605594   605595   rs80246094   G   A          23           8   
3      chr1   941118   941119    rs4372192   A   G          18          21   
4      chr1   941766   941767  rs114982608   G   A          13          17   
...     ...      ...      ...          ...  ..  ..         ...         ...   
39253  chr1  3857250  3857251   rs12126653   C   G           6          10   
39254  chr1  3900695  3900696   rs10909825   C   T          10          11   
39255  chr1  3901067  3901068    rs3935779   G   T          12          10   
39256  chr1  3901096  3901097    rs3935778   C   T          21          13   
39257  chr1  3901534  3901535   rs72849340   T   G           5           6   

       sample_id  BAD  ...  donor_health_condition  vendor_name  perturbation  \
0          72389  1.0  ...                     NaN  StemExpress      cytokine   
1          72389  1.0  ...                     NaN  StemExpress      cytokine   
2          72389  1.0  ...                     NaN  StemExpress      cytokine   
3          72389  1.0  ...                     NaN  StemExpress      cytokine   
4          72389  1.0  ...                     NaN  StemExpress      cytokine   
...          ...  ...  ...                     ...          ...           ...   
39253      80276  1.0  ...                     NaN          NaN          none   
39254      80276  1.0  ...                     NaN          NaN          none   
39255      80276  1.0  ...                     NaN          NaN          none   
39256      80276  1.0  ...                     NaN          NaN          none   
39257      80276  1.0  ...                     NaN          NaN          none   

       treatment_name treatment_details dose dose_units hotspot2_spot  \
0               IL-12             IL-12  NaN        NaN        0.2297   
1               IL-12             IL-12  NaN        NaN        0.2297   
2               IL-12             IL-12  NaN        NaN        0.2297   
3               IL-12             IL-12  NaN        NaN        0.2297   
4               IL-12             IL-12  NaN        NaN        0.2297   
...               ...               ...  ...        ...           ...   
39253       untreated         untreated  NaN        NaN        0.1833   
39254       untreated         untreated  NaN        NaN        0.1833   
39255       untreated         untreated  NaN        NaN        0.1833   
39256       untreated         untreated  NaN        NaN        0.1833   
39257       untreated         untreated  NaN        NaN        0.1833   

      nuclear_percent_duplication paired_nuclear_align  
0                         23.5324          278459478.0  
1                         23.5324          278459478.0  
2                         23.5324          278459478.0  
3                         23.5324          278459478.0  
4                         23.5324          278459478.0  
...                           ...                  ...  
39253                      2.4552           28127002.0  
39254                      2.4552           28127002.0  
39255                      2.4552           28127002.0  
39256                      2.4552           28127002.0  
39257                      2.4552           28127002.0  

[39258 rows x 46 columns]

### Transforming from 'melt' format to pivot table
Conversion from 'long' to 'wide' format, with 7 * number_of_samples columns

In [5]:
# Remove head to get melt table on all the data
test = tested_variants.head()
ptable = pd.pivot_table(test, index=['#chr', 'start', 'end', 'ID', 'ref', 'alt'], columns=['sample_id'])
ptable

BAD                         alt_counts  \
sample_id                            72386 72389 72737 72755 72756      72386   
#chr start end   ID          ref alt                                            
chr1 10108 10109 rs376007522 A   T     1.0   1.0   NaN   NaN   NaN       21.0   
     10468 10469 rs370233998 C   G     NaN   NaN   1.5   NaN   NaN        NaN   
     10588 10589 .           C   T     NaN   NaN   NaN   2.5   2.5        NaN   

                                                              ...  pval_ref  \
sample_id                            72389 72737 72755 72756  ...     72386   
#chr start end   ID          ref alt                          ...             
chr1 10108 10109 rs376007522 A   T    39.0   NaN   NaN   NaN  ...  0.999398   
     10468 10469 rs370233998 C   G     NaN   6.0   NaN   NaN  ...       NaN   
     10588 10589 .           C   T     NaN   NaN   6.0   5.0  ...       NaN   

                                                                          \
sample_id                                72389     72737     72755 72756   
#chr start end   ID          ref alt                                       
chr1 10108 10109 rs376007522 A   T    0.999866       NaN       NaN   NaN   
     10468 10469 rs370233998 C   G         NaN  0.432531       NaN   NaN   
     10588 10589 .           C   T         NaN       NaN  0.785226   1.0   

                                     ref_counts                          
sample_id                                 72386 72389 72737 72755 72756  
#chr start end   ID          ref alt                                     
chr1 10108 10109 rs376007522 A   T          6.0  14.0   NaN   NaN   NaN  
     10468 10469 rs370233998 C   G          NaN   NaN  10.0   NaN   NaN  
     10588 10589 .           C   T          NaN   NaN   NaN  10.0   5.0  

[3 rows x 30 columns]

# Data aggregation

To increase statistical power data can be aggregated in various ways, see examples below

In [48]:
## Functions to aggregate the data and calculate FDR separetely for ref and alt alleles
alleles = ('ref', 'alt')
group_columns = ['#chr', 'start', 'end', 'ID', 'ref', 'alt']
aggregation_method = 'mudholkar_george' # for the list of available methods see https://docs.scipy.org/doc/scipy/reference/generated/scipy.stats.combine_pvalues.html

def aggregate_snp(snp_df, *args, **kwargs):
    pvals = {}
    effect_sizes = {}
    for allele in alleles:
        raw_pvals = snp_df[f"pval_{allele}"].to_numpy()
        pvals[allele] = logit_aggregate_pvalues(raw_pvals)
        # Effect size alt = -1 * Effect size ref
        effect_sizes[allele] = aggregate_es(snp_df['es'].tolist(), raw_pvals)
    mean_BAD = snp_df['BAD'].mean()
    return mean_BAD, pvals, effect_sizes

def aggregate_apply(df):
    new_df = df.drop_duplicates(subset=group_columns).copy()
    mean_BAD, pvals, effect_sizes = aggregate_snp(df)
    new_df['mean_BAD'] = mean_BAD
    for allele in alleles:
        new_df[f'pval_ag_{allele}'] = pvals[allele]
    
    if pvals['ref'] < pvals['alt']:
        preference = 'ref'
    elif pvals['ref'] > pvals['alt']:
        preference = 'alt'
    else:
        preference = None
    if preference is None:
        if pd.isna(effect_sizes['ref']) and pd.isna(effect_sizes['alt']):
            new_df['es_ag'] = None
        elif effect_sizes['ref'] == effect_sizes['alt']:
            new_df['es_ag'] = 0
        else:
            new_df['es_ag'] = effect_sizes['ref']
    else:
        new_df['es_ag'] = effect_sizes[preference]
#     new_df['preference'] = preference
    new_df['# of SNPs'] = len(df.index)
    new_df['max_coverage'] = df.eval('ref_counts + alt_counts').max()
    return new_df[group_columns + ['mean_BAD', '# of SNPs', 'max_coverage', 'es_ag', 'pval_ag_ref', 'pval_ag_alt']]


def aggregate_es(es_array, p_array):
    res = [(x, y) for x, y in zip(es_array, p_array) if y != 1 and not pd.isna(y)]
    if len(res) > 0:
        es, p = zip(*res)
        weights = [-1 * np.log10(x) for x in p]
        es_mean = np.average(es, weights=weights)
    else:
        es_mean = np.nan
    return es_mean


def logit_aggregate_pvalues(pval_list):
    pvalues = np.array([pvalue for pvalue in pval_list if 1 > pvalue > 0])
    if len(pvalues) == 0:
        return 1
    elif len(pvalues) == 1:
        return pvalues[0]
    return combine_pvalues(pvalues, method=aggregation_method)[1]

def calc_fdr(aggr_df):
    for allele in alleles:
        try:
            _, pval_arr, _, _ = multipletests(aggr_df[f'pval_ag_{allele}'], alpha=0.05, method='fdr_bh')
        except TypeError:
            print(aggr_df, aggr_df[f'pval_ag_{allele}'])
            raise
        aggr_df[f"fdrp_bh_{allele}"] = pval_arr
    aggr_df['min_fdrp_bh'] = aggr_df[["fdrp_bh_ref", "fdrp_bh_alt"]].min(axis=1)
    return aggr_df

def aggregate_and_fdr(df, group_key=None, with_ray=False, show_bar=False, *args, **kwargs):
    if with_ray:
        # Parallel code, often works slower than pure pandas
        import swifter
        return df.swifter.groupby(group_columns, as_index=False, group_keys=False).apply(aggregate_apply)
    else:
        snp_groups = df.groupby(group_columns, as_index=False, group_keys=False)
        if show_bar:
            iterator = tqdm(snp_groups)
        else:
            iterator = snp_groups
        result_df = calc_fdr(pd.concat([aggregate_apply(snp_df) for snp_key, snp_df in iterator]))
        result_df['group_key'] = group_key
        return result_df

def aggregate_over_column(df, group_column=None):
    if group_column is None:
        # Aggregate over all the data
        return aggregate_and_fdr(df, show_bar=True)
    else:
        # Groupby over specified column and calculate FDR separetely for each group
        return pd.concat([aggregate_and_fdr(g_df, g_name) for g_name, g_df in tqdm(df.groupby(group_column, as_index=False))])

## Data can be grouped by various properties and then aggregated within each group.
### For example, we can group by indiv_id (samples with the same genotype), taxonomy_name (i.e. cell type), e.t.c
### Within each group variants at the same genomic position and with the same genotype (ref and alt alleles) are aggregated
### Due to unknown structural haplotypes at each variant, we perform a one-sided test for reference and alternative allele imbalance separately. This yields two significance estimates: one for each of the alleles.
### After aggregation the data has the following format:
+ `#chr, start, end`: genomic position of the SNV, hg38 genome assembly;<br>
+ `ID`: rsSNP ID of the SNV according to the dbSNP build 151;<br>
+ `ref`: reference allele (A,C,G, or T, according to hg38);<br>
+ `alt`: alternative allele
+ `mean_BAD`: average BAD score of the aggregated variants at the same genomic position
+ `# of SNPs`: number of SNVs on the same position being aggregated
+ `max_coverage`: maximal coverage among aggregated variants at the same genomic position
+ `es_ag`: aggregated effect sizes. Calculated as an average of individual effect sizes at the aggregated variants with weights being log10(P-values). N/A if all P-values in the aggregation are 1.
+ `pval_ag_ref, pval_ag_alt`: aggregated pvalues. By default we are using logit (Mudholkar-George) aggregation of pvalues.
+ `fdrp_bh_ref, fdrp_bh_alt`: Benjamini-Hochberg FDR corrected aggregated p-values for tested SNVs from the datasets in the same group
+ `min_fdrp_bh`: minimum of `fdrp_bh_ref` and `fdrp_bh_alt`
+ `group_key`: name of the aggregation group, e.g. cell type



## Examples of data aggregation

### Pull the data from the server

In [13]:
columns = ['#chr', 'start', 'end', 'ID', 'ref', 'alt', 'ref_counts', 'alt_counts',
       'sample_id', 'BAD', 'es', 'pval_ref', 'pval_alt']

# get variants in chr1:1-5000000
!tabix https://resources.altius.org/~jvierstra/projects/encode4-allelic-imbalance-v1/cav_pvalues.1010.melt.sorted.bed.gz chr1:1-5000000 > cav_pvalues.chr1_1-5000000.bed
    
tested_variants = pd.read_table('cav_pvalues.chr1_1-5000000.bed', header=None, names=columns)

# filter by coverage >= 20
tested_variants = tested_variants[tested_variants.eval('ref_counts + alt_counts >= 20')]

###  Aggregate all the data

In [49]:
aggregated_data = aggregate_over_column(tested_variants, None)
aggregated_data

  0%|          | 0/3731 [00:00<?, ?it/s]

#chr    start      end            ID ref alt  mean_BAD  # of SNPs  \
0      chr1    10108    10109   rs376007522   A   T  1.000000          2   
10     chr1   102950   102951   rs200298631   C   T  1.000000          1   
18     chr1   181112   181113  rs1383295402   A   G  1.000000          1   
19     chr1   181320   181321  rs1191715520   C   G  1.666667          6   
30     chr1   181383   181384  rs1258951683   G   C  1.500000          1   
...     ...      ...      ...           ...  ..  ..       ...        ...   
39243  chr1  4977751  4977752     rs6666330   A   G  1.500000          1   
39247  chr1  4977990  4977991    rs12739724   G   A  1.500000          3   
39250  chr1  4978032  4978033     rs6666618   A   C  1.500000          3   
39255  chr1  4984909  4984910     rs1106585   G   A  1.000000          1   
39256  chr1  4984969  4984970     rs1106586   G   A  1.500000          1   

       max_coverage     es_ag  pval_ag_ref   pval_ag_alt  fdrp_bh_ref  \
0                53 -1.618684     0.999996  2.526052e-05     1.000000   
10               35  1.321928     0.008337  9.970077e-01     0.134651   
18               28 -2.201634     1.000000  4.424427e-04     1.000000   
19              104  1.295187     0.181374  9.634122e-01     0.898679   
30               31  1.474459     0.012363  9.970303e-01     0.178099   
...             ...       ...          ...           ...          ...   
39243            41 -0.524618     0.894771  1.776924e-01     1.000000   
39247           148 -1.131160     0.999972  2.155024e-04     1.000000   
39250           162 -1.174431     1.000000  7.905153e-08     1.000000   
39255            24  0.241008     0.419653  7.298979e-01     1.000000   
39256            23  0.008538     0.570281  5.449869e-01     1.000000   

       fdrp_bh_alt  min_fdrp_bh group_key  
0         0.002693     0.002693      None  
10        1.000000     0.134651      None  
18        0.025011     0.025011      None  
19        1.000000     0.898679      None  
30        1.000000     0.178099      None  
...            ...          ...       ...  
39243     1.000000     1.000000      None  
39247     0.015462     0.015462      None  
39250     0.000014     0.000014      None  
39255     1.000000     1.000000      None  
39256     1.000000     1.000000      None  

[3731 rows x 16 columns]

### Aggregate data within each sample independently

In [50]:
aggregated_data = aggregate_over_column(tested_variants, 'sample_id')
aggregated_data

  0%|          | 0/821 [00:00<?, ?it/s]

#chr    start      end           ID ref alt  mean_BAD  # of SNPs  \
8655   chr1  1372257  1372258    rs2649597   T   C       1.0          1   
8829   chr1  1375287  1375288    rs2242398   A   C       1.0          1   
8942   chr1  1375543  1375544    rs2765033   T   C       1.0          1   
8981   chr1  1375594  1375595    rs2649594   C   T       1.0          1   
18700  chr1  2232128  2232129     rs263533   C   T       1.0          1   
...     ...      ...      ...          ...  ..  ..       ...        ...   
18795  chr1  2232128  2232129     rs263533   C   T       1.0          1   
19418  chr1  2255645  2255646     rs260508   T   G       1.0          1   
23036  chr1  2547071  2547072    rs2477678   T   A       1.0          1   
23830  chr1  2578428  2578429  rs140567883   C   G       1.0          1   
33385  chr1  3857168  3857169   rs13374773   C   A       1.0          1   

       max_coverage     es_ag  pval_ag_ref  pval_ag_alt  fdrp_bh_ref  \
8655             21  1.000000     0.094288     0.964267     0.942883   
8829             58 -0.099536     0.652998     0.447842     0.989434   
8942             84 -0.275634     0.836933     0.222602     0.989434   
8981             36 -0.485427     0.878508     0.202516     0.989434   
18700            20  0.000000     0.591064     0.591064     0.989434   
...             ...       ...          ...          ...          ...   
18795            40 -0.289507     0.785205     0.317914     0.985426   
19418            96 -0.241008     0.820801     0.237576     0.985426   
23036           129  0.067114     0.430155     0.637573     0.985426   
23830            76  0.459432     0.103368     0.932307     0.910049   
33385            26  0.222392     0.422597     0.721582     0.985426   

       fdrp_bh_alt  min_fdrp_bh  group_key  
8655      0.964267     0.942883      58668  
8829      0.895683     0.895683      58668  
8942      0.556506     0.556506      58668  
8981      0.556506     0.556506      58668  
18700     0.919564     0.919564      58668  
...            ...          ...        ...  
18795     0.635828     0.635828      80833  
19418     0.554344     0.554344      80833  
23036     0.932307     0.932307      80833  
23830     0.932307     0.910049      80833  
33385     0.932307     0.932307      80833  

[24384 rows x 16 columns]

### Aggregate data within each cell type

In [51]:
tested_variants_and_metadata = tested_variants.merge(meta, left_on='sample_id', right_on='ag_id')
aggregated_data = aggregate_over_column(tested_variants_and_metadata, 'taxonomy_name')
aggregated_data

  0%|          | 0/179 [00:00<?, ?it/s]

#chr    start      end            ID ref alt  mean_BAD  # of SNPs  \
2522   chr1   184460   184461  rs1169715936   G   A       1.0          1   
2523   chr1   778533   778534   rs570631764   A   G       1.0          1   
2524   chr1   778638   778639   rs114983708   A   G       1.0          1   
2525   chr1   827251   827252     rs3131948   T   A       1.0          1   
2526   chr1   827434   827435   rs569781818   G   A       1.0          1   
...     ...      ...      ...           ...  ..  ..       ...        ...   
21226  chr1  3857573  3857574    rs12723005   T   C       1.5          1   
21227  chr1  3857731  3857732    rs12722891   A   G       1.5          1   
21228  chr1  3857747  3857748    rs12726906   T   C       1.5          1   
21229  chr1  4267566  4267567   rs115393370   G   A       1.5          1   
21230  chr1  4379756  4379757     rs2926482   C   G       1.5          1   

       max_coverage     es_ag  pval_ag_ref  pval_ag_alt  fdrp_bh_ref  \
2522             23  1.847997     0.005075     1.000000     0.091325   
2523             30  0.000000     0.572247     0.572247     0.886596   
2524             33  1.415037     0.006765     0.997730     0.091325   
2525             20  1.584963     0.019547     1.000000     0.131942   
2526             40  0.893085     0.040345     0.980761     0.217864   
...             ...       ...          ...          ...          ...   
21226            54 -0.168614     0.727981     0.352876     0.881427   
21227            35 -0.946738     0.974283     0.057432     0.999649   
21228            27 -1.225058     0.989094     0.040977     0.999649   
21229            49  0.737200     0.066406     0.964749     0.575516   
21230            40  0.000000     0.527714     0.527714     0.833666   

       fdrp_bh_alt  min_fdrp_bh group_key  
2522      1.000000     0.091325      HMEC  
2523      1.000000     0.886596      HMEC  
2524      1.000000     0.091325      HMEC  
2525      1.000000     0.131942      HMEC  
2526      1.000000     0.217864      HMEC  
...            ...          ...       ...  
21226     0.902008     0.881427      iTH2  
21227     0.746621     0.746621      iTH2  
21228     0.710274     0.710274      iTH2  
21229     0.996795     0.575516      iTH2  
21230     0.902008     0.833666      iTH2  

[14450 rows x 16 columns]

In [55]:
# get significantly imbalanced variants with higher than two-fold effect size
aggregated_data[aggregated_data.eval('min_fdrp_bh < 0.05 & abs(es_ag) >= 1')]

#chr    start      end           ID ref alt  mean_BAD  # of SNPs  \
20120  chr1  1659113  1659114    rs7534581   A   G       1.5          1   
20121  chr1  1659208  1659209  rs150671568   C   A       1.0          1   
20122  chr1  1659219  1659220    rs9661500   A   G       1.0          1   
20125  chr1  1919745  1919746  rs113425481   G   T       1.5          1   
20130  chr1  2295715  2295716    rs4648630   G   A       1.0          1   
...     ...      ...      ...          ...  ..  ..       ...        ...   
8673   chr1  2323069  2323070   rs61762082   C   T       1.0          1   
8688   chr1  2586774  2586775  rs371199788   G   A       1.0          1   
5768   chr1   778596   778597   rs74512038   C   T       1.0          1   
5769   chr1   827475   827476  rs142969342   G   A       1.0          1   
5773   chr1  1325352  1325353     rs307346   A   C       1.0          1   

       max_coverage     es_ag  pval_ag_ref   pval_ag_alt  fdrp_bh_ref  \
20120           297 -1.250651     1.000000  2.629178e-11     1.000000   
20121           435 -1.045010     1.000000  1.864821e-13     1.000000   
20122           332 -1.013056     1.000000  3.886425e-10     1.000000   
20125            36 -2.047337     1.000000  6.320732e-04     1.000000   
20130            45 -2.000000     0.999992  3.287288e-05     1.000000   
...             ...       ...          ...           ...          ...   
8673             86 -1.127756     0.999842  3.658550e-04     1.000000   
8688            118  1.074001     0.000069  9.999685e-01     0.005737   
5768            244 -1.371969     1.000000  1.634014e-12     1.000000   
5769            324 -2.108182     1.000000  2.486780e-31     1.000000   
5773             33  1.643856     0.002275  9.993461e-01     0.024475   

        fdrp_bh_alt   min_fdrp_bh    group_key  
20120  8.150450e-10  8.150450e-10    HMVEC-LBl  
20121  1.156189e-11  1.156189e-11    HMVEC-LBl  
20122  8.031945e-09  8.031945e-09    HMVEC-LBl  
20125  6.531423e-03  6.531423e-03    HMVEC-LBl  
20130  5.095297e-04  5.095297e-04    HMVEC-LBl  
...             ...           ...          ...  
8673   3.036597e-02  3.036597e-02  h.weri-Rb-1  
8688   9.999685e-01  5.736898e-03  h.weri-Rb-1  
5768   3.513130e-11  3.513130e-11         iTH1  
5769   1.069315e-29  1.069315e-29         iTH1  
5773   9.996379e-01  2.447537e-02         iTH1  

[358 rows x 16 columns]